# Model fitting
This notebook fit different machine learning model to the dataset prepared from the OTIM database.

In [1]:
#basic data handeling and plotting
import ast
import glob
import math
import os
import pickle
import random
import plotly
import statistics
from scipy import stats
import matplotlib
import matplotlib.gridspec as gridspec
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import statsmodels.api as s
from collections import Counter
from IPython.display import Image, Markdown, display
from tqdm.notebook import tqdm, trange

#data transformation and encoding
import category_encoders as ce
import optuna
from optuna.integration import LightGBMPruningCallback
from optuna.visualization import (plot_optimization_history, plot_intermediate_values,
                                  plot_parallel_coordinate, plot_param_importances)
# if plotly graph are not showing run: "juypter labextension install juypterlab-plotly" in the terminal
from BorutaShap import BorutaShap #change shuffle to false in source code to get close to strict cv
from missingpy import MissForest  # pip install git+https://github.com/berkeleyjess/missingpy@patch-1
# modify <python direcotry>/lib/site-packages/missingpy/knninpute.py at line 11: replace "sklearn.neighbors.base" by "sklearn.neighbors._base"
from sklearn.compose import ColumnTransformer
from sklearn.impute import KNNImputer, SimpleImputer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import (
    MinMaxScaler,
    Normalizer,
    OneHotEncoder,
    StandardScaler,
)

#models
from catboost import CatBoostRegressor, Pool
from lightgbm import LGBMRegressor
from mlxtend.regressor import StackingCVRegressor
from sklearn.ensemble import (
    AdaBoostRegressor,
    ExtraTreesRegressor,
    GradientBoostingRegressor,
    RandomForestRegressor,
)
from sklearn.linear_model import ElasticNet, Lasso, LinearRegression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.tree import DecisionTreeRegressor
from xgboost import XGBRegressor
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.compose import TransformedTargetRegressor
from sklearn.preprocessing import PowerTransformer
from sklearn.ensemble import BaggingRegressor
from sklearn.ensemble import StackingRegressor

#evaluation 
import shap
from sklearn.metrics import (
    confusion_matrix,
    mean_absolute_error,
    mean_squared_error,
    r2_score,
)
from sklearn.model_selection import (
    GridSearchCV,
    KFold,
    RandomizedSearchCV,
    cross_val_predict,
    cross_val_score,
    cross_validate,
    train_test_split,
)

import warnings
warnings.simplefilter('ignore')

# working directory
data_dir = "../wd/"

# set seed for random vars as well as some basic aesthetics for plots and cv-split-number
seed = 420
tresh_outer = 10
sns.set(rc={"figure.figsize": (14, 6)}, font_scale=1.3)
sns.set_style("ticks")
# decimal output limit
%precision 3

C:\Users\gblanchy\WPy64-3890\python-3.8.9.amd64\lib\site-packages\statsmodels\tsa\base\tsa_model.py:7: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import (to_datetime, Int64Index, DatetimeIndex, Period,
C:\Users\gblanchy\WPy64-3890\python-3.8.9.amd64\lib\site-packages\statsmodels\tsa\base\tsa_model.py:7: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import (to_datetime, Int64Index, DatetimeIndex, Period,
C:\Users\gblanchy\WPy64-3890\python-3.8.9.amd64\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\gblanchy\WPy64-

'%.3f'

In [2]:
# load database
df0 = pd.read_excel(data_dir + "KunsatDB_prep.xlsx")
df = df0.drop(['Month1_sin','Month1_cos','Month2_sin','Month2_cos'],1)

## Functions
Definition of useful function, especially for the split of the data during the cross-validation.

In [3]:
def KFold_index(dataframe, tresh=10, seed=seed, shuffel=True, df_org=df, keep_dist=True, leak=False):
    """Performes a cross-fold split based on different references so there is no data-leakage in the folds.
    The user can set a number of folds as well as there should be a shuffle in the indicies (important if encoders 
    like CatBoostEncoder should be used).
    
    Parameters
    ----------
    dataframe : dataframe 
        Dataframe that should be split in k-folds. Ususally X.
        
    thresh : int
        Number of folds that should be created.
        
    seed : int
        Random seed used to reproduce same splits.
        
    shuffle : Boolean
        False if indices should not be shuffled at the end. Default is True
        
    df : dataframe
        Original dataframe used as reference, since X (used in dataframe) ususally doesnt contain information about the reference.      
        
        
    Returns:
    --------
        List of tuples each containing the indices for the test and training set of the dataframe. 
    """
    dataframe = df_org.loc[dataframe.index]  # .reset_index(drop=True)
    df_fold = ( dataframe["ReferenceTag"].value_counts().reset_index().sample(frac=1, random_state=seed) )  # get datframe with reference and value counts and shuffle this a bit to create a better distribution across folds
    df_sum = math.ceil( dataframe["ReferenceTag"].value_counts().sum() / tresh    )  # define number of entries for each fold
    df_fold["total"] = df_fold[        "ReferenceTag"    ].cumsum()  # build cumulative sum across the value counts
    df_fold["batch"] = (df_fold["total"] / df_sum).astype(        int    )  # divide cumulative sum by number of entries per fold and round them -> gives the fold number
    df_fold.loc[df_fold["batch"] > (tresh - 1), "batch"] = random.randint(        0, (tresh - 1)    )  # depending on the shuffle and value counts it occure that at the end there is a fold to much so these are randomly assignt to an other fold
    myCViterator = ([])  # store indices of folds in a lsit of multiple tuples and mybe shuffle them
    for i in df_fold["batch"].unique():
        ref_list = df_fold[df_fold["batch"] == i]["index"].to_list()
        testIndices = dataframe[dataframe["ReferenceTag"].isin(ref_list)].index.values.astype(int).tolist()
        trainIndices = dataframe[dataframe["ReferenceTag"].isin(ref_list) == False].index.values.astype(int).tolist()
        if leak:
            for idx_lst in list(dataframe[dataframe["ReferenceTag"].isin(ref_list)].reset_index().groupby("ReferenceTag")["index"].apply(list)):
                if len(idx_lst)>1:
                    trainIndices.append(idx_lst[random.randrange(len(idx_lst))])
        if shuffel:
            np.random.shuffle(trainIndices)
            np.random.shuffle(testIndices)
        myCViterator.append((trainIndices, testIndices))
    if keep_dist:
        while len(dataframe.loc[trainIndices, "cust_type"].unique()) < len(dataframe.loc[:, "cust_type"].unique()):
            seed = random.randint(0,1000)
            df_fold = ( dataframe["ReferenceTag"].value_counts().reset_index().sample(frac=1, random_state=seed)
            )  # get datframe with reference and value counts and shuffle this a bit to create a better distribution across folds
            df_sum = math.ceil( dataframe["ReferenceTag"].value_counts().sum() / tresh    )  # define number of entries for each fold
            df_fold["total"] = df_fold["ReferenceTag"].cumsum()  # build cumulative sum across the value counts
            df_fold["batch"] = (df_fold["total"] / df_sum).astype(        int    )  # divide cumulative sum by number of entries per fold and round them -> gives the fold number
            df_fold.loc[df_fold["batch"] > (tresh - 1), "batch"] = random.randint(        0, (tresh - 1)    )  # depending on the shuffle and value counts it occure that at the end there is a fold to much so these are randomly assignt to an other fold
            myCViterator = ([])  # store indices of folds in a lsit of multiple tuples and mybe shuffle them
            for i in df_fold["batch"].unique():
                ref_list = df_fold[df_fold["batch"] == i]["index"].to_list()
                testIndices = dataframe[dataframe["ReferenceTag"].isin(ref_list)].index.values.astype(int).tolist()
                trainIndices = dataframe[dataframe["ReferenceTag"].isin(ref_list) == False].index.values.astype(int).tolist()
                if leak:
                    for idx_lst in list(dataframe[dataframe["ReferenceTag"].isin(ref_list)].reset_index().groupby("ReferenceTag")["index"].apply(list)):
                        if len(idx_lst)>1:
                            trainIndices.append(idx_lst[random.randrange(len(idx_lst))])
                if shuffel:
                    np.random.shuffle(trainIndices)
                    np.random.shuffle(testIndices)
                myCViterator.append((trainIndices, testIndices))
    return myCViterator


def KFold_index_LOO(dataframe, seed=seed, shuffel=True, df_org=df):
    """Performes a leave on out cross-fold split based on different references so there is no data-leakage in the folds.
    The user can set if there should be a shuffle in the indicies (important if encoders like CatBoostEncoder should be used).
    
    Parameters
    ----------
    dataframe : dataframe 
        Dataframe that should be split in k-folds. Ususally X.
        
    seed : int
        Random seed used to reproduce same splits.
        
    shuffle : Boolean
        False if indices should not be shuffled at the end. Default is True
        
    df : dataframe
        Original dataframe used as reference, since X (used in dataframe) ususally doesnt contain information about the reference.      
        
        
    Returns:
    --------
        List of tuples each containing the indices for the test and training set of the dataframe. 
    """
    dataframe = df_org.loc[dataframe.index]  # .reset_index(drop=True)
    myCViterator = []
    for i in dataframe["ReferenceTag"].unique():
        trainIndices = dataframe[dataframe["ReferenceTag"] != i].index.values.astype(
            int
        )
        testIndices = dataframe[dataframe["ReferenceTag"] == i].index.values.astype(int)
        if shuffel:
            np.random.shuffle(trainIndices)
            np.random.shuffle(testIndices)
        myCViterator.append((trainIndices, testIndices))
    return myCViterator


# list of simple helper functions to get dataframes of single values aout of list and/or dict

def cv_df(list_RMSE, list_R2):
    df = pd.DataFrame([list_RMSE, list_R2], index=["RMSE", "R2"])
    df_mean = df.mean(axis=1)
    df_mean.name = "mean"
    df_std = df.std(axis=1)
    df_std.name = "std"
    df_all = pd.concat([df, df_mean, df_std], axis=1)
    return df_all

def get_df_score_all(model_dict, i):
    df = pd.melt(
        model_dict[i]["df_RMSE_R2"].transpose().iloc[:-2],
        var_name="scoring2",
        value_name="value",
    )
    df["model"] = i
    return df

def shap_plot(j, model, df):
    explainerModel = shap.TreeExplainer(model)
    shap_values_Model = explainerModel.shap_values(df)
    p = shap.force_plot(explainerModel.expected_value, shap_values_Model[j], df.iloc[[j]])
    return(p)

def ABS_SHAP(df_shap,df):
    # Make a copy of the input data
    shap_v = df_shap
    feature_list = df.columns
    shap_v.columns = feature_list
    df_v = df.copy()
    
    # Determine the correlation in order to plot with different colors
    corr_list = list()
    for i in feature_list:
        b = np.corrcoef(shap_v[i],df_v[i])[1][0]
        corr_list.append(b)
    corr_df = pd.concat([pd.Series(feature_list),pd.Series(corr_list)],axis=1).fillna(0)
    # Make a data frame. Column 1 is the feature, and Column 2 is the correlation coefficient
    corr_df.columns  = ['Variable','Corr']
    corr_df['Sign'] = np.where(corr_df['Corr']>0,'red','blue')
    
    # Plot it
    shap_abs = np.abs(shap_v)
    k=pd.DataFrame(shap_abs.mean()).reset_index()
    k.columns = ['Variable','SHAP_abs']
    k2 = k.merge(corr_df,left_on = 'Variable',right_on='Variable',how='inner')
    k2 = k2.sort_values(by='SHAP_abs',ascending = True)
    colorlist = k2['Sign']
    ax = k2.plot.barh(x='Variable',y='SHAP_abs',color = colorlist, figsize=(5,6),legend=False)
    ax.set_xlabel("SHAP Value (Red = Positive Impact)")
    
def kMeansRes(scaled_data, k, alpha_k=0.02):
    '''
    Parameters 
    ----------
    scaled_data: matrix 
        scaled data. rows are samples and columns are features for clustering
    k: int
        current k for applying KMeans
    alpha_k: float
        manually tuned factor that gives penalty to the number of clusters
    Returns 
    -------
    scaled_inertia: float
        scaled inertia value for current k           
    '''
    
    inertia_o = np.square((scaled_data - scaled_data.mean(axis=0))).sum()
    # fit k-means
    kmeans = KMeans(n_clusters=k, random_state=0).fit(scaled_data)
    scaled_inertia = kmeans.inertia_ / inertia_o + alpha_k * k
    return scaled_inertia


def chooseBestKforKMeans(scaled_data, k_range):
    """
    """
    ans = []
    for k in k_range:
        scaled_inertia = kMeansRes(scaled_data, k)
        ans.append((k, scaled_inertia))
    results = pd.DataFrame(ans, columns = ['k','Scaled Inertia']).set_index('k')
    best_k = results.idxmin()[0]
    return best_k, results

def df_add_K(X, y, df_org, clean=True):
    """
    Steps:
    - inputation on missing values (MissingForest)
    - K mean clustering all imputed values
    - add the Kmean to the datafarme
    - PCA analysis
    - delete outliers which are out based on the first two components
    """
    encoder = ce.CatBoostEncoder(handle_unknown="return_nan", handle_missing="return_nan")
    X_trans_full = encoder.fit_transform(X, y)
    imputer = MissForest(n_jobs=8, n_estimators=100, random_state=seed)
    X_imp = pd.DataFrame(imputer.fit_transform(X_trans_full), columns=X.columns)
    k_range = range(2, 20)
    best_k, results = chooseBestKforKMeans(np.matrix(X_imp), k_range)
    kmeans = KMeans(n_clusters=best_k)
    kmeans.fit(X_imp)
    X['cust_type'] = kmeans.predict(X_imp)
    df_org["cust_type"] = X['cust_type']
    pca = PCA(2)
    X_pca = pca.fit_transform(X_imp)
    label = kmeans.fit_predict(X_pca)
    k_df = pd.concat([pd.DataFrame(X_pca),pd.DataFrame(label, columns=["k"])], axis=1)
    if clean == True:
        for i in pd.DataFrame(kmeans.cluster_centers_).index:
            if abs(pd.DataFrame(kmeans.cluster_centers_).loc[i, 0]) > pd.DataFrame(kmeans.cluster_centers_)[0].mean()+pd.DataFrame(kmeans.cluster_centers_)[0].std()*2 or abs(pd.DataFrame(kmeans.cluster_centers_).loc[i, 1]) > pd.DataFrame(kmeans.cluster_centers_)[1].mean()+pd.DataFrame(kmeans.cluster_centers_)[1].std()*2:
                k_idx = k_df[k_df["k"]==i].index
                print('deleting {:d} outliers entries'.format(len(k_idx)))
                X.drop(index=k_idx).reset_index(drop=True, inplace=True)
                y.drop(index=k_idx).reset_index(drop=True, inplace=True)
                df_org.drop(index=k_idx).reset_index(drop=True, inplace=True)

def get_best_features(df, min_number_features=5, max_number_features=12):
    """
    """
    df = df[df["num_features"].between(min_number_features, max_number_features)]
    return df[df["val_metric_mean"] == df["val_metric_mean"].max()].iloc[0]

def get_df_predictions(K_dict_pred, K_dict_cv, K_value):
    """Compute absolute error (AE) based on predicted and observed values.
    
    Parameters
    ----------
    K_dict_pred : dict
        Dictionnary of predicted values??
    K_dict_cv : dict
        Dictionary of CV scores??
    K_value : str
        Key for indexing the other dictionnary. Name of the target variable.
    """
    df = pd.concat([K_dict_pred[K_value]["predictions"], K_dict_cv[K_value][10]], axis=1)
    df["AE"] = abs(df[K_value+"_y_test"] - df[K_value+"_prediction"])
    lst_idx = []
    shift_val = len(K_dict_cv[K_value][10]) - len(K_dict_pred[K_value]["predictions"])
    for i in df[[K_value, K_value+"_y_test"]].index:
        if df.loc[i, K_value] != df.loc[i, K_value+"_y_test"]:
            lst_idx.append(i)
    if len(lst_idx)>0:
        df.loc[range(lst_idx[0], len(df)), [K_value+"_y_test", K_value+"_prediction"]] = df.loc[range(lst_idx[0], len(df)), [K_value+"_y_test", K_value+"_prediction"]].shift(shift_val)
    return df

def r2_rmse( g ):
    """Compute root mean squared error from dictionnary with keys 'test' and 'predictions'.
    
    Parameters
    ----------
    g : dict
        Dictionnary with keys 'test' and 'predictions' which contains list-like of numeric values.
    """
    r2 = r2_score( g['test'], g['predictions'] )
    rmse = np.sqrt( mean_squared_error( g['test'], g['predictions'] ) )
    return pd.Series( dict(  R2 = r2, RMSE = rmse ) )


## Preparation
- computing weights based on number of replicates and number of entries per reference
- set all K > Ks to Ks

In [4]:
# create weight and K Range as columns
inan = df['Reps'].isna()
print('{:d} nan in Reps set to 1'.format(np.sum(inan)))
df.loc[inan, 'Reps'] = 1
for i in df.index:
    df.loc[i,"weight"] = (df.loc[i, "Reps"] / statistics.sqrt(len(df[df["ReferenceTag"]==df.loc[i,"ReferenceTag"]])))

#for i in df.index:
#    for k in ['Ks', "k1", 'k2', 'k3', 'k4', 'k5', 'k6', 'k7', 'k8', 'k9', 'k10']:
#        df.loc[i, "range_"+k] = df[df["ReferenceTag"]==df.loc[i,"ReferenceTag"]]["log_"+k].max() - df[df["ReferenceTag"]==df.loc[i,"ReferenceTag"]]["log_"+k].min()

18 nan in Reps set to 1


In [5]:
# create list for subsets of variables for model and visualization

climate_factors_temp = [
    "Latitude",
    "Longitude",
    "AnnualMeanTemperature",
    "MeanTemperatureofWarmestQuarter",
    "MeanTemperatureofColdestQuarter",
    "Isothermality",
    "TemperatureSeasonality",
    "MaxTemperatureofWarmestMonth",
    "MinTemperatureofColdestMonth",
    "TemperatureAnnualRange",
    "MeanTemperatureofWettestQuarter",
    "MeanTemperatureofDriestQuarter"
]

climate_factors_per = [
    "Latitude",
    "Longitude",
    "AnnualPrecipitation",
    "PrecipitationofWettestMonth",
    "PrecipitationofDriestMonth",
    "PrecipitationSeasonality",
    "PrecipitationofWettestQuarter",
    "PrecipitationofDriestQuarter",
    "PrecipitationofWarmestQuarter",
    "PrecipitationofColdestQuarter",
    "MeanDiurnalRange",
    "AverageAridityIndex",
    "AverageAnnualEvapoTranspiration",
    #"AridityClass",
]

soil_factors = [
    #"SoilTextureFAO",
    "SoilTextureUSDA",
#    "SoilTypeClass", # actually classified and interpolated for unknown in SoilTypeWRB
    "SoilTypeWRB",
    "ClayContent",
    "SiltContent",
    "SandContent",
    "BulkDensity",
    "SoilOrganicCarbon",
]

method_factors = [
    "Season_sin",
    "Season_cos",
    #"Month1_sin",
    #"Month1_cos",
    #"Month2_sin",
    #"Month2_cos",
    "Method",
    "Direction",
    "UpperD_m",
    "Diameter"
]

management_factors = [
    "LanduseClass",
    "TillageClass",
    "NbOfCropRotation",
    "CropClass",
    "CoverCropClass",
    "ResidueClass",
    "GrazingClass",
    "IrrigationClass",
    "CompactionClass",
    "SamplingTimeClass",
    "AmendmentClass",
    "ContainsCereals",
    "ContainsFallow",
    "ContainsGrassHerbs",
    "ContainsLegume",
    "ContainsMaize",
    "ContainsTreesFruits",
    "ContainsVegetables",
]

k_factors = [
    "log_Ks",
    "log_K1",
    "log_K2",
    "log_K3",
    "log_K4",
    "log_K5",
    "log_K6",
    "log_K7",
    "log_K8",
    "log_K9",
    "log_K10"
]

## Preparation log_Kx
- keeping columns with at least 70% non-missing values
- filter outliers with z-score > 3

In [6]:
# merge columns and create a target variable
combine_cols = (
    climate_factors_per
    + climate_factors_temp
    + method_factors
    + soil_factors
    + management_factors
    + ["ReferenceTag", "ExID", "weight"]
    + k_factors
)

importantColumns = []

for i in combine_cols:
    if i not in importantColumns:
        importantColumns.append(i)

In [7]:
# only keep column where R2 > 0.9, which are not organic soil and with data above 0.3 m depth
i2keep = df['R2'].ge(0.9) & df['SoilTextureFAO'].ne('organic') & df['UpperD_m'].le(0.3)
df = df[i2keep]
# clean columns (only keep colums with more than 70% non-null values)
df_id = df[k_factors].dropna().index
df_simple = df.loc[df_id, importantColumns].reset_index(drop=True)
s = df_simple.notnull().sum()/df_simple.shape[0]
dico = s[s < 0.65].to_dict()
print('REMOVED: ', ', '.join(['{:s} ({:.2f})'.format(b, dico[b]) for b in dico.keys()]))
df_simple.dropna(thresh=int(len(df_simple) * 0.667), axis=1, inplace=True)
df_simple.info()

REMOVED:  CoverCropClass (0.04), ResidueClass (0.62), GrazingClass (0.40), IrrigationClass (0.41), CompactionClass (0.16), AmendmentClass (0.43)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 334 entries, 0 to 333
Data columns (total 62 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Latitude                         334 non-null    float64
 1   Longitude                        334 non-null    float64
 2   AnnualPrecipitation              334 non-null    float64
 3   PrecipitationofWettestMonth      334 non-null    float64
 4   PrecipitationofDriestMonth       334 non-null    float64
 5   PrecipitationSeasonality         334 non-null    float64
 6   PrecipitationofWettestQuarter    334 non-null    float64
 7   PrecipitationofDriestQuarter     334 non-null    float64
 8   PrecipitationofWarmestQuarter    334 non-null    float64
 9   PrecipitationofColdestQuarter    334 non-null    float64
 10  M

In [8]:
# create list with numeric and categorical variables and define target and predictors

pred_obj = (
    df_simple.drop(["ReferenceTag"], axis=1)
    .select_dtypes(include=["object"])
    .columns.to_list()
)
pred_num = (
    df_simple.drop(k_factors, axis=1)
    .select_dtypes(include=["float64", "int64"])
    .columns.to_list()
)

ya = df_simple[k_factors]
X = df_simple[pred_obj + pred_num]

In [9]:
# delete outliers Z > 3 and add Kmeans cluster value with clean of extreme cluster values
#i2keep = (np.abs(stats.zscore(y)) < 3) 
#print('{:d} entries out from z-score'.format(np.sum(~i2keep)))
#print(df_simple[~i2keep]['ReferenceTag'].tolist())
#df_simple = df_simple[i2keep].reset_index(drop=True)
#X = X[i2keep].reset_index(drop=True)
#y = y[i2keep].reset_index(drop=True)

#df_add_K(X, y, df_simple, clean=False)  # add Kmeans cluster value with potential clean of extreme cluster values

In [10]:
# there remains NaN as we don't do heavy imputation and some models below don't like it
X.isna().sum()[X.isna().sum()  > 0]

Method                4
Direction            15
LanduseClass          1
TillageClass          7
CropClass            88
SamplingTimeClass    51
Season_sin           46
Season_cos           46
Diameter             40
ClayContent          11
SiltContent          13
SandContent          13
BulkDensity          66
dtype: int64

## Feature selection and hyper-paremeters optimization + evaluation in nested loop
The outer loop is used for validation. The inner loop helps to define hyper-parameters and important features.

The optimization is done in 3 steps:
- soft hyper-parameter optimization with optuna
- feature selection with Boruta SHAP
- hard hyper-parameter optimization on the selected features with optuna

Remarks:
- slight "leakage" inside optuna objective as the val_set is passed to LGBMRegressor for early stopping but is also used to score the model
- boruta is not done using cross-validation (CV)

In [11]:
for k in k_factors:
        
    target = k
    y=ya[target]

    # SHOULD BE IN THE LOOP we encode all categorical features
    encoder = ce.CatBoostEncoder(handle_unknown="return_nan", handle_missing="return_nan")
    Xe = encoder.fit_transform(X, y)

    # SHOULD BE IN THE LOOP Boruta cannot deal with missing values so we need to impute the missing ones
    imputer = MissForest(n_jobs=8, n_estimators=100, random_state=seed)
    Xe = pd.DataFrame(imputer.fit_transform(Xe), columns=Xe.columns)
    
    Xey = pd.concat([Xe, y], axis=1)
    Xey.to_csv(data_dir + target + '_encoded.csv', index=False) 
    
    Xy = pd.concat([X, y], axis=1)
    Xy.to_csv(data_dir + target + '_original.csv', index=False) 


Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 5
Iteration: 6
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3


In [12]:
# define objetive function with a given set of hyperparameters
def objective(trial, X, y, cv):
    
    params = {
        "n_estimators": 2000, #trial.suggest_int("n_estimators", 100, 2000, step=50),
        "num_leaves": trial.suggest_int("num_leaves", 3, 51, step=3),
        "learning_rate": 0.075, #trial.suggest_float("learning_rate", 0.01, 0.2, log=True),
        "max_depth": 4, #trial.suggest_int("max_depth", 3, 5, step=1),
        "random_state": seed,
        "n_jobs": -1,
        "num_iterations": 200,
        "max_bin": 16, #trial.suggest_int("max_bin", 4, 32, step=4),
        "min_child_samples": trial.suggest_int("min_child_samples", 30, 70, step=5),
        "reg_alpha": 0.001, #trial.suggest_float("reg_alpha", 0.0001, 0.01, log=True),
        "reg_lambda": 0.001, #trial.suggest_float("reg_lambda", 0.0001, 0.01, log=True),
        "min_split_gain": trial.suggest_float("min_split_gain", 0.01, 3, log=True),
        "verbose": -100,
        "boosting_type": "gbdt" # not important according to OPTUNA             
    }

    cv_scores = np.empty(len(cv))
    for idx, (train_idx, test_idx) in enumerate(cv):
        
        X_train, X_test = X.loc[train_idx, :], X.loc[test_idx, :]
        y_train, y_test = y[train_idx], y[test_idx]

        #encoder = ce.CatBoostEncoder(handle_unknown="return_nan", handle_missing="return_nan")
        #X_train = encoder.fit_transform(X_train, y_train)
        #X_test = encoder.transform(X_test)

        model = LGBMRegressor(**params)  # change the model here?
        model.fit(
            X_train.drop(["weight", "ExID"], axis=1),
            y_train,
            eval_set=[(X_test.drop(["weight", "ExID"], axis=1), y_test)],
            eval_metric='rmse', #{'r2': r2_score},
            early_stopping_rounds=500,  # stops after 100 model iterations if performance stays the same
            callbacks=[
                LightGBMPruningCallback(trial, "rmse")
            ],  # Add a pruning callback
            sample_weight = X_train["weight"],
            verbose=False
        )
        preds = model.predict(X_test.drop(["weight", "ExID"], axis=1))
        cv_scores[idx] = mean_squared_error(y_test, preds, squared=False)
    
    return np.max(cv_scores)

In [13]:
# create three different foldings for optimization and merge them together
# it reduces the effect of just falling on a bad fold

rseed = 42
number_of_folds = 10
cv_opt = KFold_index(X, tresh=number_of_folds, df_org=df_simple, seed=rseed, keep_dist=False, leak=False)

cv_naive = KFold(n_splits=number_of_folds, shuffle=True, random_state=seed)
cv_naive = cv_naive.split(X) #step needed to keep following loop consistent for all evaluation techniques

# check for ref leakage within the foldings
for fold in [cv_opt]:
    for i in range(0, tresh_outer):
        count = 0
        if (
            len(
                set(df_simple.loc[fold[i][1], "ReferenceTag"])
                & set(df_simple.loc[fold[i][0], "ReferenceTag"])
            )
            > 0
        ):
            print(str(i) + ": leakage")
            count = count + 1
    if count < 1:
        print("No Leakage")
    
       


No Leakage


In [14]:
 for k in k_factors:
        
    target = k
    y=ya[target]

    # SHOULD BE IN THE LOOP we encode all categorical features
    encoder = ce.CatBoostEncoder(handle_unknown="return_nan", handle_missing="return_nan")
    Xe = encoder.fit_transform(X, y)

    # SHOULD BE IN THE LOOP Boruta cannot deal with missing values so we need to impute the missing ones
    imputer = MissForest(n_jobs=8, n_estimators=100, random_state=seed)
    Xe = pd.DataFrame(imputer.fit_transform(Xe), columns=Xe.columns)

    universalR2_collec = []
    medianGlobalR2_collec = []
    localR2_collec = []

    for i in list(range(0, 10)):
        #####################################################################################################
        # using optuna and Boruta for feature selection in a nested way (15 min with 5 trials, 20 buruta and 20 study2)
        #####################################################################################################

        rseed = i
        number_of_folds = 10
        #cv_opt = KFold_index(X, tresh=number_of_folds, df_org=df_simple, seed=rseed, keep_dist=False, leak=False)

        cv_naive = KFold(n_splits=number_of_folds, shuffle=True, random_state=rseed)
        cv_naive = cv_naive.split(Xe) #step needed to keep following loop consistent for all evaluation techniques
        cv_opt = ([])
        for icalc, itest in cv_naive:
             cv_opt.append((list(icalc), list(itest)))

        # check for ref leakage within the foldings
        # for fold in [cv_opt]:
        #     for ii in range(0, tresh_outer):
        #         count = 0
        #         if (
        #             len(
        #                 set(df_simple.loc[fold[ii][1], "ReferenceTag"])
        #                 & set(df_simple.loc[fold[ii][0], "ReferenceTag"])
        #             )
        #             > 0
        #         ):
        #             print(str(ii) + ": leakage")
        #             count = count + 1
        #     if count < 1:
        #         print("No Leakage")

        studies = []
        misfits = []
        feats = []
        exp_val_list = []
        shap_list = []
        corr_list = []
        dffeat = pd.DataFrame(columns=Xe.drop(['weight', 'ExID'], axis=1).columns)
        dfout = pd.DataFrame()
        params = {'verbose': -1}
        cvnow = cv_opt
        itas = 50
     
        # the outer loop provide the test set that hasn't been used for parameter
        # training or for hyper-parameter validation
        cc=0
        Xec = Xe.drop(['weight', 'ExID'], axis=1)
        for icalc, itest in tqdm(cvnow): # TODO could make this in parallel
            dic = {}
            cc=cc+1
   
            # print(" ")
            # print(" ")
            # print(" ")
            # print("******************************************************************************************")
            # print("******************************************************************************************")
            # print("Processing fold #" + str(cc))
            # print("******************************************************************************************")
            # print("******************************************************************************************")
            # print(" ")
            # print(" ")
            # print(" ")

            # the inner cv split between training (parameter) and validation (for hyper-parameters)
            # cv_inner = KFold_index(Xe.loc[icalc, :], tresh=tresh_outer, df_org=df_simple, seed=seed, keep_dist=False, leak=False)
            # cv_inner = cv_inner    
            
            cv_inner0 = KFold(n_splits=number_of_folds, shuffle=True, random_state=rseed)
            cv_inner0 = cv_inner0.split(Xe.iloc[icalc, :])                         
            cv_inner = []
            for icalc2, itest2 in cv_inner0:
                cv_inner.append((list(icalc2), list(itest2)))
 
            # first optimization with optuna
            study1 = optuna.create_study(
                sampler=optuna.samplers.TPESampler(),
                pruner=optuna.pruners.PatientPruner(
                    optuna.pruners.MedianPruner(n_startup_trials=2, n_warmup_steps=15, interval_steps=5),
                    patience=1),
                direction="minimize", # PUT maximize if R2 is chosen
            )
            def func1(trial):
                #return objective(trial, Xe.loc[icalc, :], y[icalc], cv=cv_inner)
                return objective(trial, Xe.loc[icalc, :].reset_index(drop=True), y[icalc].reset_index(drop=True), cv=cv_inner)  #use this one for naive CV
            study1.optimize(func1, n_trials=itas)  # optimize
            for key in study1.best_params:
                dic['study1_' + key] = study1.best_params[key]
            dic['study1_val'] = study1.best_value

            # using the best set of hyper-parameters, we do feature selection
            feat_selector = BorutaShap(
                model = LGBMRegressor(**study1.best_params, random_state=seed, n_jobs=-1),
                importance_measure="shap",
                classification=False,
            )
            feat_selector.fit(X=Xec.loc[icalc, :], y=y[icalc], n_trials=20, 
                                    sample=False, train_or_test="test", verbose=False, normalize=False)
            selec = feat_selector.accepted + feat_selector.tentative
            feats.append(selec)

            # hard optimization based on the selected feature
            study2 = optuna.create_study(
                sampler=optuna.samplers.TPESampler(),
                pruner=optuna.pruners.PatientPruner(
                    optuna.pruners.MedianPruner(n_startup_trials=2, n_warmup_steps=15, interval_steps=5),
                    patience=1),
                direction="minimize", # PUT maximize if R2 is chosen
            )
            def func2(trial):
                # this time, only selected feature are in
                #return objective(trial, Xe.loc[icalc, selec + ['weight', 'ExID']], y[icalc], cv=cv_inner)
                return objective(trial, Xe.loc[icalc, selec + ['weight', 'ExID']].reset_index(drop=True), y[icalc].reset_index(drop=True), cv=cv_inner) #use this one for naive CV
            study2.optimize(func2, n_trials=itas)  # optimize
            for key in study2.best_params:
                dic['study2_' + key] = study2.best_params[key]
            dic['study2_val'] = study2.best_value
            studies.append(study2)

            # fit the model with the selected feature and best hyper-parameters found
            model = LGBMRegressor(**study2.best_params, random_state=seed, n_jobs=1)
            model.fit(Xec.loc[icalc, selec], y[icalc],
        #            eval_set=[(X_test.drop(["weight", "ExID"], axis=1), y_test)],
        #            eval_metric='rmse', #{'r2': r2_score},
        #            early_stopping_rounds=10,  # stops after 100 model iterations if performance stays the same
        #            callbacks=[
        #                LightGBMPruningCallback(trial, "rmse")
        #            ],  # Add a pruning callback
                    sample_weight = Xe.loc[icalc, "weight"],
                    verbose=False)
            # also here, not sure if it's better to fit the model on icalc or just take the best model fitted on itrain?
            # or take the best_estimator from study2?

            # evaluation
            meanSRTest = np.mean((y[itest] - model.predict(Xec.loc[itest, selec]))**2)
            meanSSTrain = np.mean((y[icalc] - np.mean(y[icalc]))**2)
            dic['rmse_train'] = mean_squared_error(y[icalc], model.predict(Xec.loc[icalc, selec]))
            dic['rmse_test'] = mean_squared_error(y[itest], model.predict(Xec.loc[itest, selec]))
            dic['r2_train'] = r2_score(y[icalc], model.predict(Xec.loc[icalc, selec]))
            dic['r2_test'] = r2_score(y[itest], model.predict(Xec.loc[itest, selec]))
            dic['glob_r2_test'] = 1 - meanSRTest / meanSSTrain
            misfits.append( (y[itest] - model.predict(Xec.loc[itest, selec]) ))
            dfout = dfout.append(dic, ignore_index=True)

            explainer = shap.TreeExplainer(model)
            exp_val_list.append(explainer.expected_value)
            shap_values = pd.DataFrame(explainer.shap_values(Xec[selec]), 
                                           columns=Xec[selec].columns)
            shap_list.append(shap_values)
            
            corr_list = list()
            for coco in selec:
                b = np.corrcoef(shap_values[coco],Xec[coco])[1][0]
                corr_list.append(b)
            corr_df = pd.concat([pd.Series(selec),pd.Series(corr_list)],axis=1).fillna(0)
            # Make a data frame. Column 1 is the feature, and Column 2 is the correlation coefficient
            corr_df.columns  = ['Variable','Corr']
            corr_list.append(corr_df)
            
        ##############################################################################
        #optimize and train a final model to get feature importance    
        ##############################################################################    

        print(" ")
        print(" ")
        print(" ")
        print("$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$")
        print("$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$")
        print("Training final model of iteration " + str(i+1) + " of 10 ...")
        print("$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$")
        print("$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$$")
        print(" ")
        print(" ")
        print(" ")       

        kuntz = Counter(np.hstack(feats))
        freaqs = {k: c for k, c in kuntz.items() if c >= 5}
        selec = list(freaqs.keys())

        study3 = optuna.create_study(
            sampler=optuna.samplers.TPESampler(),
            pruner=optuna.pruners.PatientPruner(
                optuna.pruners.MedianPruner(n_startup_trials=2, n_warmup_steps=15, interval_steps=5),
                patience=1),
            direction="minimize", # PUT maximize if R2 is chosen
        )

        def func3(trial):
            # this time, only selected feature are in
            return objective(trial, Xe.loc[:, selec + ['weight', 'ExID']], y, cv=cvnow)
        study3.optimize(func3, n_trials=itas)  # optimize
        for key in study3.best_params:
            dic['study3_' + key] = study3.best_params[key]

        finalModel =  model = LGBMRegressor(**study3.best_params, random_state=seed, n_jobs=1)
        finalModel.fit(Xec.loc[:, selec], y,
            sample_weight = Xe.loc[:, "weight"],
            verbose=False)
        explainer = shap.TreeExplainer(model)
        shap_values = pd.DataFrame(explainer.shap_values(Xec[selec]), 
            columns=Xec[selec].columns)

        print(" ")
        print("Done! : ) ")
        print(" ")

        #sort results
        dfout.sort_values('r2_test', ascending=False)

        valiRMSE = []
        for j in range (len(studies)): 
            valiRMSE.append(studies[j].best_trial.values)

        #sort results
        dfout.sort_values('r2_test', ascending=False)

        #calc measures of goodness of prediction
        globalRMedSquares = np.sqrt(np.median((y - np.mean(y))**2))
        RMSE = np.sqrt(np.mean(np.hstack(misfits)**2))
        meanValiRMSE = np.mean(valiRMSE)
        RMedSE = np.sqrt(np.median(np.hstack(misfits)**2))
        universalR2 = 1 - np.sum( np.hstack(misfits)**2 ) / np.sum( (y - np.mean(y))**2 )
        
        universalR2_collec.append(universalR2)
        medianGlobalR2_collec.append(dfout['glob_r2_test'].median())
        localR2_collec.append(dfout['r2_test'].median())

        #save data
        dfout.to_csv(data_dir + target + '_run' + str(i) + '.csv', index=False)
        shap_values.to_csv(data_dir + target + 'GlobalShaps_run' + str(i) + '.csv', index=False)
        Xec[selec].to_csv(data_dir + target + 'XecSelec_run' + str(i) + '.csv', index=False)
        with open(data_dir + target + 'LocalShapList_run' + str(i) + '.pkl', 'wb') as f:
            pickle.dump(shap_list, f)
        with open(data_dir + target + 'LocalExpValuesList_run' + str(i) + '.pkl', 'wb') as f:
            pickle.dump(exp_val_list, f)
        with open(data_dir + target + 'LocalCorrList_run' + str(i) + '.pkl', 'wb') as f:
            pickle.dump(corr_list, f)
    
    #save summerized data
    a1 = pd.DataFrame(universalR2_collec, columns = ['universal R2'])
    a2 = pd.DataFrame(medianGlobalR2_collec, columns = ['median global R2'])
    a3 = pd.DataFrame(localR2_collec, columns = ['median local R2'])
    dfsum = pd.concat([a1, a2, a3], axis=1)
    dfsum.to_csv(data_dir + target + 'R2Summary_run' + str(i) + '.csv', index=False)

Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3


  0%|          | 0/10 [00:00<?, ?it/s]

[I 2022-05-05 19:43:20,834] A new study created in memory with name: no-name-a226d88c-12ad-4729-aae4-2f9bbff1193c
[I 2022-05-05 19:43:21,555] Trial 0 finished with value: 0.482093312415466 and parameters: {'num_leaves': 9, 'min_child_samples': 40, 'min_split_gain': 1.2172739438603182}. Best is trial 0 with value: 0.482093312415466.
[I 2022-05-05 19:43:22,354] Trial 1 finished with value: 0.4728109763222064 and parameters: {'num_leaves': 9, 'min_child_samples': 70, 'min_split_gain': 0.04308645996850596}. Best is trial 1 with value: 0.4728109763222064.
[I 2022-05-05 19:43:23,293] Trial 2 finished with value: 0.4196896002751703 and parameters: {'num_leaves': 48, 'min_child_samples': 45, 'min_split_gain': 0.029482628136547163}. Best is trial 2 with value: 0.4196896002751703.
[I 2022-05-05 19:43:23,324] Trial 3 pruned. Trial was pruned at iteration 60.
[I 2022-05-05 19:43:23,358] Trial 4 pruned. Trial was pruned at iteration 80.
[I 2022-05-05 19:43:23,384] Trial 5 pruned. Trial was pruned a

  0%|          | 0/20 [00:00<?, ?it/s]

[I 2022-05-05 19:43:39,837] A new study created in memory with name: no-name-9fc87a44-155a-4b93-8fc6-a659170bac65
[I 2022-05-05 19:43:40,596] Trial 0 finished with value: 0.4673654347995412 and parameters: {'num_leaves': 42, 'min_child_samples': 65, 'min_split_gain': 0.17916096927336353}. Best is trial 0 with value: 0.4673654347995412.
[I 2022-05-05 19:43:41,302] Trial 1 finished with value: 0.483663756794225 and parameters: {'num_leaves': 15, 'min_child_samples': 50, 'min_split_gain': 1.0929542184749919}. Best is trial 0 with value: 0.4673654347995412.
[I 2022-05-05 19:43:41,987] Trial 2 finished with value: 0.5362506423463649 and parameters: {'num_leaves': 36, 'min_child_samples': 70, 'min_split_gain': 1.7245871901276524}. Best is trial 0 with value: 0.4673654347995412.
[I 2022-05-05 19:43:42,780] Trial 3 finished with value: 0.4936516772767856 and parameters: {'num_leaves': 6, 'min_child_samples': 60, 'min_split_gain': 1.1970034132131013}. Best is trial 0 with value: 0.4673654347995

...

[I 2022-05-05 23:41:10,233] Trial 0 finished with value: 0.49242775408793477 and parameters: {'num_leaves': 36, 'min_child_samples': 45, 'min_split_gain': 0.23277247537875978}. Best is trial 0 with value: 0.49242775408793477.
[I 2022-05-05 23:41:10,663] Trial 1 finished with value: 0.5986068524276945 and parameters: {'num_leaves': 45, 'min_child_samples': 45, 'min_split_gain': 2.1585267312702903}. Best is trial 0 with value: 0.49242775408793477.
[I 2022-05-05 23:41:11,201] Trial 2 finished with value: 0.428199491180183 and parameters: {'num_leaves': 21, 'min_child_samples': 50, 'min_split_gain': 0.03708150080991967}. Best is trial 2 with value: 0.428199491180183.
[I 2022-05-05 23:41:11,699] Trial 3 finished with value: 0.4461044114385133 and parameters: {'num_leaves': 12, 'min_child_samples': 70, 'min_split_gain': 0.08180462382086899}. Best is trial 2 with value: 0.428199491180183.
[I 2022-05-05 23:41:11,714] Trial 4 pruned. Trial was pruned at iteration 65.
[I 2022-05-05 23:41:11,736]

 
Done! : ) 
 


  0%|          | 0/10 [00:00<?, ?it/s]

[I 2022-05-06 07:34:37,341] A new study created in memory with name: no-name-ee8ed61c-1f75-40df-83c3-77170d2145ae
[I 2022-05-06 07:34:38,053] Trial 0 finished with value: 0.5516432376418161 and parameters: {'num_leaves': 39, 'min_child_samples': 50, 'min_split_gain': 1.181936549218038}. Best is trial 0 with value: 0.5516432376418161.
[I 2022-05-06 07:34:38,815] Trial 1 finished with value: 0.4523518709608258 and parameters: {'num_leaves': 3, 'min_child_samples': 60, 'min_split_gain': 0.09432897022957497}. Best is trial 1 with value: 0.4523518709608258.
[I 2022-05-06 07:34:39,638] Trial 2 finished with value: 0.4751090105267238 and parameters: {'num_leaves': 18, 'min_child_samples': 70, 'min_split_gain': 0.3014668905532194}. Best is trial 1 with value: 0.4523518709608258.
[I 2022-05-06 07:34:39,693] Trial 3 pruned. Trial was pruned at iteration 120.
[I 2022-05-06 07:34:40,705] Trial 4 finished with value: 0.4632140704315971 and parameters: {'num_leaves': 15, 'min_child_samples': 70, 'mi

KeyboardInterrupt: 

In [ ]:
print(localR2_collec)
print(medianGlobalR2_collec)
print(universalR2_collec)
print(" ")
print("mean local R2 = " + str(np.mean(localR2_collec)) + " with a sd of " + str(np.std(localR2_collec)))
print("mean global R2 = " + str(np.mean(medianGlobalR2_collec)) + " with a sd of " + str(np.std(medianGlobalR2_collec)))
print("mean universal R2 = " + str(np.mean(universalR2_collec)) + " with a sd of " + str(np.std(universalR2_collec)))

In [ ]:
valiRMSE = []
for i in range (len(studies)): 
    valiRMSE.append(studies[i].best_trial.values)
    
#sort results
dfout.sort_values('r2_test', ascending=False)

#calc measures of goodness of prediction
globalRMedSquares = np.sqrt(np.median((y - np.mean(y))**2))
RMSE = np.sqrt(np.mean(np.hstack(misfits)**2))
meanValiRMSE = np.mean(valiRMSE)
RMedSE = np.sqrt(np.median(np.hstack(misfits)**2))
globalR2 = 1 - np.sum(np.hstack(misfits)**2)/np.sum((y - np.mean(y))**2)
globalM2 = 1 - RMedSE / globalRMedSquares

#save data
dfout.to_csv(data_dir + 'K10_dfout2022-01-20.csv', index=False)

#print(dfout)
print("mean training RMSE = ", str(dfout['rmse_train'].mean()))
print("validation RMSE = ", str(meanValiRMSE))
print("mean testing RMSE = ", str(dfout['rmse_test'].mean()))
print("global testing RMSE = ", str(RMSE))
print("RMedSE = ", str(RMedSE))
print("median local R2 = ", str(dfout['r2_test'].median()))
print("median global R2 = ", str(dfout['glob_r2_test'].median()))
print("global R2 = ", str(globalR2))

ABS_SHAP(shap_values, Xec[selec])
dfout

In [ ]:
# histogram of the squared residuals
fig, ax = plt.subplots()
for misfit in misfits:
    ax.hist(misfit**2, bins=np.linspace(0, 5, 20), edgecolor='k', alpha=0.1)
ax.set_ylabel('Frequency')
ax.set_xlabel('Squared residuals');

Since the number of entries and the number of NA in the columns varies across different K values the cleaning and preparation has to be done separate. Imputed and encoded Splits are stored in a file to use later the same splits with a feature selection.